# Lab 14 - Hypothesis testing with multiple categories

In Labs 12 and 13, we looked at categorical data with two categories (Smoker/Non-smoker, Black/Non-Black, Purple/White).  In this lab we will learn how to test hypotheses when our categorical data has more than two categories.

First, let's import the necessary libraries.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
%matplotlib inline

### Jury Panels in Alameda Country 2009-2010

We will look at jury panel data from 2009 and 2010 collected by the American Civil Liberties Union (ACLU).  The total number of people who reported for jury duty in those years was 1,452.  See [11.2 Multiple Categories](https://www.inferentialthinking.com/chapters/11/2/Multiple_Categories.html) for more information.

We can create a dataframe with this data as shown below. 

In [ ]:
# create a dictionary listing each column, followed by the column values in a list
jury_data = {"Eligible":[0.15, 0.18, 0.12, 0.54, 0.01],
             "Panels":[0.26, 0.08, 0.08, 0.54, 0.04]}
# pass the dictionary into the dataframe creation function as a parameter
# also pass in labels for the rows
jury = pd.DataFrame(data = jury_data, index = ["Asian","Black","Latinx","White","Other"])

What do you think are the columns and rows of the new dataframe?  Check your answer by displaying the dataframe `jury`. 

We will now make a bar chart of the two columns of data.  Because our dataframe `jury` already contains counts of the different categories, we do not have to use the `value_count()` function. Instead, type `jury.plot(kind = "bar")` below.

How does the distribution of eligible jurors compare with the distribution of the jury panels?

To know whether the variation between the distributions is just the result of chance, we can compute a random sample from the eligible distribution and compare it with the panel distribution.

As in Labs 12 and 13, create a variable for the eligible population and distribution

<details> <summary>Answer:</summary>
    <code>population = ["Asian","Black","Latinx","White","Other"]
pop_prob = [0.15, 0.18, 0.12, 0.54, 0.01]</code>
</details>

Create a sample from this population.  The sample should be the same size as our data.

<details> <summary>Answer:</summary>
    <code>sample = np.random.choice(population,p = pop_prob,size = 1453)</code>
</details>

Compute the value counts for the sample.  Since we only have the probabilities of the eligible population, we want to compute the value counts as probabilities as well.  We can do this by adding the parameter `normalize = True`.  Save the probabilities of the sample in the variable `sample_probs`.

<details> <summary>Answer:</summary>
    <code>sample_probs = pd.Series(sample).value_counts(normalize = True)
</code>
</details>

Next we will create a new column in our dataframe called `Random` that contains the probabilities from our random sample.  To do this, type `jury["Random"] = sample_probs` below and run it.

Display the `jury` dataframe again to check that the column was added.

Plot the bar chart of the dataframe again, and the new column will be included.

<details> <summary>Answer:</summary>
    <code>jury.plot(kind = "bar")</code>
</details>

How does the distribution of the random sample compare to the eligible distribution?  To the panel distribution?

Let's compare the panels distribution to the eligible distribution quantitatively using hypothesis testing.  We need to choose a statistic to simulate, called the *test statistic*.  In this problem, we will use something called the *Total Variation Distance (TVD)* as the test statistic.  The TVD measures the difference between two distributions.  

First we will compute the TVD between the panels and eligible distribution:

In [ ]:
jury["Difference"] = jury["Panels"] - jury["Eligible"]
jury

What is the sum of the difference column?  

To fix this, we will take the absolute differences between probabilities.

In [ ]:
jury["Absolute Difference"] = np.abs(jury["Difference"])
jury

What does this do?

Now take the sum of the absolute difference column.  You can use the same command as when we took the sum of a filter.

In [ ]:
jury["Absolute Difference"].sum()

<details> <summary>Answer:</summary>
    <code>jury["Absolute Difference"].sum()
</code>
</details>

Notice this sum is twice either the positive or negative count, so we divide it by two.  This quantity is the *total variation distance (TVD)* between the distribution of ethnicity in the eligible juror population and the panel.

In [ ]:
data_tvd = jury["Absolute Difference"].sum()/2
data_tvd

We could have done this calculation in one line of code:
`np.abs(jury["Panel"] - jury["Eligible"]).sum()/2`
Try it below.

Next we want to understand the distribution of the test statistic (here, the TVD) if the panels were actually from the eligible distribution.  To do this, we want to simulate random samples from the eligible distribution and compute the total variation distance between the sample and eligible distribution.

First compute for one random sample, and compute the TVD between its probabilities and the eligible distribution.

<details> <summary>Answer:</summary>
    <code>sample = np.random.choice(population,p = pop_prob,size = 1453)
sample_probs = pd.Series(sample).value_counts(normalize = True)
jury["Random"] = sample_probs
sample_tvd = np.abs(jury["Random"] - jury["Eligible"]).sum()/2
</code>
</details>

Now we want to repeat this process many times, and make a histogram of the difference TVD values.  First, use a loop to generate many samples and compute the TVD to the eligible population.

<details> <summary>Answer:</summary>
    <code>tvds = []
for i in range(10000):
    sample = np.random.choice(population,p = pop_prob,size = 1453)
    sample_probs = pd.Series(sample).value_counts(normalize = True)
    jury["Random"] = sample_probs
    sample_tvd = np.abs(jury["Random"] - jury["Eligible"]).sum()/2
    tvds.append(sample_tvd)
</code>
</details>

Next make the histogram of these simulated test statistics (the TVDs).

<details> <summary>Answer:</summary>
    <code>pd.Series(tvds).hist()
</code>
</details>

Does the test statistic computed from the data look like it comes from this distribution?

###  The borough distribution of 311 calls revisited

In Lab 11, we qualitatively compared the distribution of the boroughs for Sunday March 3 and Monday March 4 for 311 complaints and service requests.  We will now use hypothesis testing to quantitatively compare these distributions.

Null hypothesis:  The distribution of boroughs for which 311 calls are made is the same on Sunday and Monday.

Alternative hypothesis:  The distribution of boroughs for which 311 calls are made is different on Sunday than on Monday.

Load your CSV file with call data from March 3 and 4, 2019 into the dataframe `calls`.  Read the `Created Date` column in as a date/time.

Display the `calls` dataframe to make sure it was loaded into memory correctly.

The code from Lab 11 to create the overlapping bar charts is below.